In [2]:
import shutil 
import os
import subprocess
import re
import pybedtools
import math


In [42]:
# inputs
input_file1= "/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R1_001.fastq"
input_file2= "/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R2_001.fastq"
coordinate_file="operon_region.bed" #   gene_region.bed     operon_region.bed     genome_region.bed
min_frag_size=50
min_frag_len_pair=140
output_bed_final = "output.RNA-RNA_operon_noChim_50-140.bed" #####
output_junction1_final="RNA-RNA_read_1_junction.bed"
output_junction2_final="RNA-RNA_read_2_junction.bed"



'''
RNA-RNA
/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R1_001.fastq
/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R2_001.fastq

DNA-DNA
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_interaction/S11_R1.fastq
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_interaction/S11_R2.fastq

DNA-RNA
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-RNA_interaction/S14_S14_R1_001.fastq
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-RNA_interaction/S14_S14_R2_001.fastq

RNA-RNA EXTRA
/mnt/c/Users/99alb/OneDrive/Desktop/RNA-RNA_extra/S03_S3_R1_001.fastq
/mnt/c/Users/99alb/OneDrive/Desktop/RNA-RNA_extra/S03_S3_R2_001.fastq

DNA-DNA EXTRA
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_extra/S10_S10_R1_001.fastq
/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_extra/S10_S10_R2_001.fastq

DNA-DNA Bacillus


'''


'\nRNA-RNA\n/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R1_001.fastq\n/mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R2_001.fastq\n\nDNA-DNA\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_interaction/S11_R1.fastq\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_interaction/S11_R2.fastq\n\nDNA-RNA\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-RNA_interaction/S14_S14_R1_001.fastq\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-RNA_interaction/S14_S14_R2_001.fastq\n\nRNA-RNA EXTRA\n/mnt/c/Users/99alb/OneDrive/Desktop/RNA-RNA_extra/S03_S3_R1_001.fastq\n/mnt/c/Users/99alb/OneDrive/Desktop/RNA-RNA_extra/S03_S3_R2_001.fastq\n\nDNA-DNA EXTRA\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_extra/S10_S10_R1_001.fastq\n/mnt/c/Users/99alb/OneDrive/Desktop/DNA-DNA_extra/S10_S10_R2_001.fastq\n\nDNA-DNA Bacillus\n\n\n'

In [4]:
import subprocess

# List of commands to execute
commands = [
f"trimmomatic PE -phred33 -threads 8 {input_file1} {input_file2} R1_clean_paired.fastq R1_clean_unpaired.fastq R2_clean_paired.fastq R2_clean_unpaired.fastq ILLUMINACLIP:/mnt/c/Users/99alb/OneDrive/Desktop/data/TruSeq3-PE-2.fa:2:30:7:8:true LEADING:25 TRAILING:20 SLIDINGWINDOW:4:15 MINLEN:30"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")


TrimmomaticPE: Started with arguments:
 -phred33 -threads 8 /mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R1_001.fastq /mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R2_001.fastq R1_clean_paired.fastq R1_clean_unpaired.fastq R2_clean_paired.fastq R2_clean_unpaired.fastq ILLUMINACLIP:/mnt/c/Users/99alb/OneDrive/Desktop/data/TruSeq3-PE-2.fa:2:30:7:8:true LEADING:25 TRAILING:20 SLIDINGWINDOW:4:15 MINLEN:30
Using PrefixPair: 'TACACTCTTTCCCTACACGACGCTCTTCCGATCT' and 'GTGACTGGAGTTCAGACGTGTGCTCTTCCGATCT'
Using Long Clipping Sequence: 'AGATCGGAAGAGCGTCGTGTAGGGAAAGAGTGTA'
Using Long Clipping Sequence: 'AGATCGGAAGAGCACACGTCTGAACTCCAGTCAC'
Using Long Clipping Sequence: 'GTGACTGGAGTTCAGACGTGTGCTCTTCCGATCT'
Using Long Clipping Sequence: 'TACACTCTTTCCCTACACGACGCTCTTCCGATCT'
ILLUMINACLIP: Using 1 prefix pairs, 4 forward/reverse sequences, 0 forward only sequences, 0 reverse only sequences


Command 'trimmomatic PE -phred33 -threads 8 /mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R1_001.fastq /mnt/c/Users/99alb/OneDrive/Desktop/data/S01_R2_001.fastq R1_clean_paired.fastq R1_clean_unpaired.fastq R2_clean_paired.fastq R2_clean_unpaired.fastq ILLUMINACLIP:/mnt/c/Users/99alb/OneDrive/Desktop/data/TruSeq3-PE-2.fa:2:30:7:8:true LEADING:25 TRAILING:20 SLIDINGWINDOW:4:15 MINLEN:30' executed successfully.


Input Read Pairs: 19566338 Both Surviving: 19076724 (97.50%) Forward Only Surviving: 193025 (0.99%) Reverse Only Surviving: 120985 (0.62%) Dropped: 175604 (0.90%)
TrimmomaticPE: Completed successfully


In [5]:
# 178.a remove PCR duplicates from pair end
# PE
def remove_pcr_duplicates(read1_fq, read2_fq, read1_rmDup_fq, read2_rmDup_fq):
    unique = {}
    try:
        with open(read1_fq, 'r') as RA, open(read2_fq, 'r') as RB, \
             open(read1_rmDup_fq, 'w') as OA, open(read2_rmDup_fq, 'w') as OB:
            
            for id_a, id_b, seq_a, seq_b, symbol_a, symbol_b, qual_a, qual_b in zip(RA, RB, RA, RB, RA, RB, RA, RB):
                whole_reads = seq_a + seq_b
                if whole_reads in unique:
                    continue
                else:
                    OA.write(id_a + seq_a + symbol_a + qual_a)
                    OB.write(id_b + seq_b + symbol_b + qual_b)
                    unique[whole_reads] = 1
    except FileNotFoundError:
        print("Error: One of the input files not found.")

remove_pcr_duplicates('R1_clean_paired.fastq', 'R2_clean_paired.fastq', "r1.rmDup.pair.fq", "r2.rmDup.pair.fq")


    

In [6]:
# 178.b remove PCR duplicated from single end
# SE
def remove_pcr_duplicates_single_end(read1_fq, read1_rmDup_fq):
    unique = {}
    try:
        with open(read1_fq, 'r') as RA, open(read1_rmDup_fq, 'w') as OA:
            for id_a, seq_a, symbol_a, qual_a in zip(RA, RA, RA, RA):
                whole_reads = seq_a
                if whole_reads in unique:
                    continue
                else:
                    OA.write(id_a + seq_a + symbol_a + qual_a)
                    unique[whole_reads] = 1
    except FileNotFoundError:
        print("Error: One of the input files not found.")

remove_pcr_duplicates_single_end('R1_clean_unpaired.fastq', "r1.rmDup.unpair.fq")
remove_pcr_duplicates_single_end('R2_clean_unpaired.fastq', "r2.rmDup.unpair.fq")

commands = ['rm R1_clean_paired.fastq', 'rm R2_clean_paired.fastq', "rm R1_clean_unpaired.fastq", "rm R2_clean_unpaired.fastq"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")


Command 'rm R1_clean_paired.fastq' executed successfully.
Command 'rm R2_clean_paired.fastq' executed successfully.
Command 'rm R1_clean_unpaired.fastq' executed successfully.
Command 'rm R2_clean_unpaired.fastq' executed successfully.


In [7]:
# 178.c concatenate files 
import shutil
def concatenate_files(input_files, output_file):
    try:
        with open(output_file, 'wb') as out_file:
            for input_file in input_files:
                with open(input_file, 'rb') as in_file:
                    shutil.copyfileobj(in_file, out_file)
    except FileNotFoundError:
        print("Error: One of the input files not found.")
        
input_files1 = ["r1.rmDup.pair.fq", "r1.rmDup.unpair.fq"]
output_file1 = "read1.clean.rmDup.fq"
input_files2 = ["r2.rmDup.pair.fq", "r2.rmDup.unpair.fq"]
output_file2 = "read2.clean.rmDup.fq"
concatenate_files(input_files1, output_file1)
concatenate_files(input_files2, output_file2)


commands = ['rm r1.rmDup.pair.fq', 'rm r1.rmDup.unpair.fq', "rm r2.rmDup.pair.fq", "rm r2.rmDup.unpair.fq"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm r1.rmDup.pair.fq' executed successfully.
Command 'rm r1.rmDup.unpair.fq' executed successfully.
Command 'rm r2.rmDup.pair.fq' executed successfully.
Command 'rm r2.rmDup.unpair.fq' executed successfully.


In [8]:
# 179 trim low complexity regions

import subprocess

# List of commands to execute
commands = [
    "cutadapt -j 10 -b A{100} -b C{100} -b G{100} -b T{100} -n 3 --minimum-length=30 -e 0.1 -o read1.clean.rmDup.rmPoly.fq read1.clean.rmDup.fq",
    "cutadapt -j 10 -b A{100} -b C{100} -b G{100} -b T{100} -n 3 --minimum-length=30 -e 0.1 -o read2.clean.rmDup.rmPoly.fq read2.clean.rmDup.fq"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")


commands = ['rm read1.clean.rmDup.fq', 'rm read2.clean.rmDup.fq']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

This is cutadapt 4.9 with Python 3.12.2
Command line parameters: -j 10 -b A{100} -b C{100} -b G{100} -b T{100} -n 3 --minimum-length=30 -e 0.1 -o read1.clean.rmDup.rmPoly.fq read1.clean.rmDup.fq
Processing single-end reads on 10 cores ...
Finished in 61.954 s (4.494 µs/read; 13.35 M reads/minute).

=== Summary ===

Total reads processed:              13,785,344
Reads with adapters:                 1,676,304 (12.2%)

== Read fate breakdown ==
Reads that were too short:               4,946 (0.0%)
Reads written (passing filters):    13,780,398 (100.0%)

Total basepairs processed: 1,038,564,006 bp
Total written (filtered):  1,032,308,171 bp (99.4%)

=== Adapter 1 ===

Sequence: AAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAA; Type: variable 5'/3'; Length: 100; Trimmed: 268008 times
60735 times, it overlapped the 5' end of a read
207273 times, it overlapped the 3' end or was within the read

Minimum overlap: 3
No. of allowed errors:
1-9 b

In [9]:
# 180/181 map

import subprocess

# List of commands to execute
commands = [
    "STAR --runMode alignReads --genomeDir genome_index --readFilesIn read1.clean.rmDup.rmPoly.fq --outFileNamePrefix read_1_toGenome_ --outSAMtype BAM SortedByCoordinate --chimOutType SeparateSAMold Junctions --outSAMattributes All --alignIntronMin 1 --scoreGapNoncan -4 --scoreGapATAC -4 --chimSegmentMin 13 --chimJunctionOverhangMin 15 --runThreadN 8 --limitBAMsortRAM 1093619191",
    "STAR --runMode alignReads --genomeDir genome_index --readFilesIn read2.clean.rmDup.rmPoly.fq --outFileNamePrefix read_2_toGenome_ --outSAMtype BAM SortedByCoordinate --chimOutType SeparateSAMold Junctions --outSAMattributes All --alignIntronMin 1 --scoreGapNoncan -4 --scoreGapATAC -4 --chimSegmentMin 13 --chimJunctionOverhangMin 15 --runThreadN 8 --limitBAMsortRAM 1093619191"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")


#genome folder
# STAR --runThreadN 6 --runMode genomeGenerate --genomeDir genome_index --genomeSAindexNbases 8 --genomeFastaFiles /mnt/c/Users/99alb/OneDrive/Desktop/data/ec.fasta

commands = ['rm read1.clean.rmDup.rmPoly.fq', 'rm read2.clean.rmDup.rmPoly.fq']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")


	/home/albe/miniconda3/bin/STAR-avx2 --runMode alignReads --genomeDir genome_index --readFilesIn read1.clean.rmDup.rmPoly.fq --outFileNamePrefix read_1_toGenome_ --outSAMtype BAM SortedByCoordinate --chimOutType SeparateSAMold Junctions --outSAMattributes All --alignIntronMin 1 --scoreGapNoncan -4 --scoreGapATAC -4 --chimSegmentMin 13 --chimJunctionOverhangMin 15 --runThreadN 8 --limitBAMsortRAM 1093619191
	STAR version: 2.7.11b   compiled: 2024-07-03T14:39:20+0000 :/opt/conda/conda-bld/star_1720017372352/work/source
Sep 02 16:45:41 ..... started STAR run
Sep 02 16:45:41 ..... loading genome
Sep 02 16:45:41 ..... started mapping
Sep 02 16:47:44 ..... finished mapping
Sep 02 16:47:44 ..... started sorting BAM
Sep 02 16:48:07 ..... finished successfully
Command 'STAR --runMode alignReads --genomeDir genome_index --readFilesIn read1.clean.rmDup.rmPoly.fq --outFileNamePrefix read_1_toGenome_ --outSAMtype BAM SortedByCoordinate --chimOutType SeparateSAMold Junctions --outSAMattributes All -

In [10]:
"""def from_jun_to_bed(input_file, output_file):
        with open(input_file, 'r') as ipp, open(output_file, 'w') as out_file:
            out_file.write("track graphType=arc\n")
            for line in ipp:
                sub = line.split()
                out_file.write(f"{sub[0]}\t{sub[1]}\t{sub[4]}\n")
                
from_jun_to_bed('read_1_toGenome_Chimeric.out.junction',f'{output_junction1_final}')
from_jun_to_bed('read_2_toGenome_Chimeric.out.junction',f'{output_junction2_final}')"""

'def from_jun_to_bed(input_file, output_file):\n        with open(input_file, \'r\') as ipp, open(output_file, \'w\') as out_file:\n            out_file.write("track graphType=arc\n")\n            for line in ipp:\n                sub = line.split()\n                out_file.write(f"{sub[0]}\t{sub[1]}\t{sub[4]}\n")\n                \nfrom_jun_to_bed(\'read_1_toGenome_Chimeric.out.junction\',f\'{output_junction1_final}\')\nfrom_jun_to_bed(\'read_2_toGenome_Chimeric.out.junction\',f\'{output_junction2_final}\')'

In [11]:
#182 

# conda install samtools
def process_sam_files(read1_align_sam, read2_align_sam, num_of_cpu):

    prefix_read1_align = os.path.splitext(read1_align_sam)[0]
    prefix_read2_align = os.path.splitext(read2_align_sam)[0]

# Convert SAM to BAM
#    subprocess.run(f"samtools view -@ {num_of_cpu} -b -S -o {prefix_read1_align}.bam {read1_align_sam}", shell=True, check=True)
#    subprocess.run(f"samtools view -@ {num_of_cpu} -b -S -o {prefix_read2_align}.bam {read2_align_sam}", shell=True, check=True)

    # Sort BAM files
    subprocess.run(f"samtools sort -@ {num_of_cpu} {prefix_read1_align}.bam -o {prefix_read1_align}.sort.bam", shell=True, check=True)
    subprocess.run(f"samtools sort -@ {num_of_cpu} {prefix_read2_align}.bam -o {prefix_read2_align}.sort.bam", shell=True, check=True)

    # Filter unique alignments
    #filter mapping quality = 30, -h is to include the header, -F to exclude secondary alignments with 256-flag
    subprocess.run(f"samtools view -@ {num_of_cpu} -h -q 30 -F 256 -o {prefix_read1_align}.sort.uniq.sam {prefix_read1_align}.sort.bam", shell=True, check=True)   
    subprocess.run(f"samtools view -@ {num_of_cpu} -h -q 30 -F 256 -o {prefix_read2_align}.sort.uniq.sam {prefix_read2_align}.sort.bam", shell=True, check=True)

# usage:
process_sam_files("read_1_toGenome_Aligned.sortedByCoord.out.bam", "read_2_toGenome_Aligned.sortedByCoord.out.bam", "4") # change number of cpu if it doesn't work

#output read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam // read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam

#dont delete this, it is needed later
#read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam // read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam


commands = ['rm read_1_toGenome_Aligned.sortedByCoord.out.bam', 'rm read_2_toGenome_Aligned.sortedByCoord.out.bam', "rm read_1_toGenome_Aligned.sortedByCoord.out.sort.bam", "rm read_2_toGenome_Aligned.sortedByCoord.out.sort.bam"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

[bam_sort_core] merging from 1 files and 4 in-memory blocks...
[bam_sort_core] merging from 1 files and 4 in-memory blocks...


Command 'rm read_1_toGenome_Aligned.sortedByCoord.out.bam' executed successfully.
Command 'rm read_2_toGenome_Aligned.sortedByCoord.out.bam' executed successfully.
Command 'rm read_1_toGenome_Aligned.sortedByCoord.out.sort.bam' executed successfully.
Command 'rm read_2_toGenome_Aligned.sortedByCoord.out.sort.bam' executed successfully.


In [12]:
# obtain_pairs_from_pair.pl


#extract reads that are common to both files
def extract_common_pairs(align_sam_1, align_sam_2):
    # Check if input files exist
    if not (os.path.exists(align_sam_1) and os.path.exists(align_sam_2)):
        print("Input files not found.")
        return
    
    # Pair id
    all_pairs_id = set()

    # Read headers
    sam_head = header(align_sam_1)

    # Get common pair ids
    common_id = all_id(align_sam_1).intersection(all_id(align_sam_2))

    # Output common pairs
    out(align_sam_1, "interaction_from_pair_mapped_reads_1.sam", common_id, sam_head)
    out(align_sam_2, "interaction_from_pair_mapped_reads_2.sam", common_id, sam_head)

def out(sam, out_file, common_id, sam_head):
    with open(out_file, "w") as out_file_handle:
        out_file_handle.write(sam_head)
        with open(sam, "r") as sam_file_handle:
            for line in sam_file_handle:
                if line.startswith('@'):
                    continue
                read_id = line.split()[0]
                if read_id in common_id:
                    out_file_handle.write(line)

def header(sam):
    header_lines = []
    with open(sam, "r") as sam_file:
        for line in sam_file:
            if line.startswith('@'):
                header_lines.append(line)
            else:
                break
    return ''.join(header_lines)

def all_id(sam):
    common_id = set()
    with open(sam, "r") as sam_file:
        for line in sam_file:
            if not line.startswith('@'):
                read_id = line.split()[0]
                common_id.add(read_id)
    return common_id

# usage:
extract_common_pairs("read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam", "read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam")

#output: interaction_from_pair_mapped_reads_1.sam // interaction_from_pair_mapped_reads_2.sam


In [13]:
# use interaction_from_pair_mapped_reads_1.sam interaction_from_pair_mapped_reads_2.sam
def process_sam_files_interaction(read1_align_sam, read2_align_sam, num_of_cpu):
    prefix_read1_align = os.path.splitext(read1_align_sam)[0]
    prefix_read2_align = os.path.splitext(read2_align_sam)[0]

    # Convert SAM to BAM
    subprocess.run(f"samtools view -@ {num_of_cpu} -b -S -o {prefix_read1_align}.bam {read1_align_sam}", shell=True, check=True)
    subprocess.run(f"samtools view -@ {num_of_cpu} -b -S -o {prefix_read2_align}.bam {read2_align_sam}", shell=True, check=True)

    # Sort BAM files
    subprocess.run(f"samtools sort -n -@ {num_of_cpu} {prefix_read1_align}.bam -o {prefix_read1_align}.sort.bam", shell=True, check=True)
    subprocess.run(f"samtools sort -n -@ {num_of_cpu} {prefix_read2_align}.bam -o {prefix_read2_align}.sort.bam", shell=True, check=True)

    # Filter unique alignments
    subprocess.run(f"samtools view -@ {num_of_cpu} -h -o {prefix_read1_align}.sort.sam {prefix_read1_align}.sort.bam", shell=True, check=True)
    subprocess.run(f"samtools view -@ {num_of_cpu} -h -o {prefix_read2_align}.sort.sam {prefix_read2_align}.sort.bam", shell=True, check=True)
    

process_sam_files_interaction("interaction_from_pair_mapped_reads_1.sam", "interaction_from_pair_mapped_reads_2.sam", "8")
# output interaction_from_pair_mapped_reads_1.sort.sam // interaction_from_pair_mapped_reads_2.sort.sam

commands = ['rm interaction_from_pair_mapped_reads_1.sam', 'rm interaction_from_pair_mapped_reads_2.sam', "rm interaction_from_pair_mapped_reads_1.bam", "rm interaction_from_pair_mapped_reads_2.bam", "rm interaction_from_pair_mapped_reads_1.sort.bam", "rm interaction_from_pair_mapped_reads_2.sort.bam"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

[bam_sort_core] merging from 0 files and 8 in-memory blocks...
[bam_sort_core] merging from 0 files and 8 in-memory blocks...


Command 'rm interaction_from_pair_mapped_reads_1.sam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_2.sam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_1.bam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_2.bam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_1.sort.bam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_2.sort.bam' executed successfully.


In [71]:
"""# precess_Chimeric_sam.pl


#identify reads that appear exactly twice and then modifies these reads by prepending Head_ to the first occurrence and Tail_ to the second occurrence
def process_chimeric_sam(sam_file, output_file):
    flag=1
    # Dictionary to store read IDs and their occurrences
    reads_id = {}

    # List to store modified SAM lines
    modified_lines = []

    # First pass: Count occurrences of each read ID
    with open(sam_file, 'r') as file:
        for line in file:
            if not line.startswith('@'):
                read_id = line.split()[0]
                reads_id[read_id] = reads_id.get(read_id, 0) + 1

    # Second pass: Process SAM file and store modified lines
    with open(sam_file, 'r') as file:
        for line in file:
            if line.startswith('@'):
                modified_lines.append(line)
            else:
                parts = line.split()
                read_id = parts[0]
                if reads_id.get(read_id, 0) == 2:
                    if flag:
                        modified_lines.append(f'Head_{line}')
                        flag = 0
                    else:
                        modified_lines.append(f'Tail_{line}')
                        flag = 1

    # Write modified lines to output file
    with open(output_file, 'w') as outfile:
        for line in modified_lines:
            outfile.write(line)


process_chimeric_sam("read_1_toGenome_Chimeric.out.sam", "read_1_toGenome_Chimeric.processed.sam")
process_chimeric_sam("read_2_toGenome_Chimeric.out.sam", "read_2_toGenome_Chimeric.processed.sam")

#output read_1_toGenome_Chimeric.processed.sam // read_2_toGenome_Chimeric.processed.sam


commands = ['rm read_1_toGenome_Chimeric.out.sam', 'rm read_2_toGenome_Chimeric.out.sam']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")"""
    
    
commands = [
    "rm read_1_toGenome_Chimeric.out.sam",
    "rm read_2_toGenome_Chimeric.out.sam"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")

Command 'rm read_1_toGenome_Chimeric.out.sam' executed successfully.
Command 'rm read_2_toGenome_Chimeric.out.sam' executed successfully.


In [15]:
import subprocess

# List of commands to execute
commands = [
    "rm interaction_from_gapped_reads.sam",
    "rm num_of_interactions_from_part.list"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")


An error occurred while executing 'rm interaction_from_gapped_reads.sam': Command 'rm interaction_from_gapped_reads.sam' returned non-zero exit status 1.
An error occurred while executing 'rm num_of_interactions_from_part.list': Command 'rm num_of_interactions_from_part.list' returned non-zero exit status 1.


rm: cannot remove 'interaction_from_gapped_reads.sam': No such file or directory
rm: cannot remove 'num_of_interactions_from_part.list': No such file or directory


In [16]:
# obtain_pairs_from_gapped_reads.pl 

def process_sam_files(align_sam_1, align_sam_2, chimeric_sam_1, chimeric_sam_2, out_sam):
    def parse_cigar(cigar):
        """
        Parse CIGAR string into a list of operations.
        """
        return re.findall(r'(\d+)([MIDNSHP=X])', cigar)

    def header(sam_file):
        """
        Extract header lines from a SAM file.
        """
        headers = []
        with open(sam_file, 'r') as file:
            for line in file:
                if line.startswith('@'):
                    headers.append(line)
                else:
                    break
        return ''.join(headers)

    def pair_part(sam_file, output_handle):
        """
        Process SAM file to handle paired reads.
        """
        count = 0
        with open(sam_file, 'r') as file:
            for line in file:
                if line.startswith('@'):
                    continue
                else:
                    parts = line.strip().split('\t')
                    cigar = parts[5]
                    start_in_read = 0
                    start_in_genome = int(parts[3])
                    
                    cigar_blocks = cigar.split('N')

                    for i in range(len(cigar_blocks) - 1):
                        end_in_read = start_in_read
                        end_in_genome = start_in_genome - 1
                        left_part = cigar_blocks[i]
                        gap_part = None
                        if re.search(r'(\d+)$', left_part):
                            gap_part = int(re.search(r'(\d+)$', left_part).group(1))
                            left_part = re.sub(r'(\d+)$', '', left_part)
                        else:
                            raise ValueError("Unexpected CIGAR format")
                        
                        right_part = re.sub(r'\d+$', '', cigar_blocks[i + 1])

                        # Process left part
                        for length, op in parse_cigar(left_part):
                            length = int(length)
                            if op == 'M':
                                end_in_read += length
                                end_in_genome += length
                            elif op == 'I':
                                end_in_read += length
                            elif op == 'D':
                                end_in_genome += length
                            elif op in {'S', 'H'}:
                                end_in_read += length

                        output_handle.write(f"{parts[0]}\t{parts[1]}\t{parts[2]}\t{start_in_genome}\t255\t{left_part}\t*\t0\t0\t")
                        output_handle.write(f"{parts[9][start_in_read:end_in_read]}\t")
                        output_handle.write(f"{parts[10][start_in_read:end_in_read]}\n")

                        # Handle gap
                        start_in_read = end_in_read
                        start_in_genome = end_in_genome + gap_part

                        # Process right part
                        for length, op in parse_cigar(right_part):
                            length = int(length)
                            if op == 'M':
                                end_in_read += length
                                end_in_genome += length
                            elif op == 'I':
                                end_in_read += length
                            elif op == 'D':
                                end_in_genome += length
                            elif op in {'S', 'H'}:
                                end_in_read += length

                        output_handle.write(f"{parts[0]}\t{parts[1]}\t{parts[2]}\t{start_in_genome + 1}\t255\t{right_part}\t*\t0\t0\t")
                        output_handle.write(f"{parts[9][start_in_read:end_in_read]}\t")
                        output_handle.write(f"{parts[10][start_in_read:end_in_read]}\n")

                        start_in_genome += 1
                        count += 1
        return count

    with open(out_sam, 'w') as outs, open('num_of_interactions_from_part.list', 'w') as num:
        # Write header
        sam_head = header(align_sam_1)
        outs.write(sam_head)

        # Process each SAM file
        count = pair_part(align_sam_1, outs)
        num.write(f"Part_from_Align_Read1:\t{count}\n")
        
        count = pair_part(align_sam_2, outs)
        num.write(f"Part_from_Align_Read2:\t{count}\n")
        
        count = pair_part(chimeric_sam_1, outs)
        num.write(f"Part_from_Chimeric_Read1:\t{count}\n")
        
        count = pair_part(chimeric_sam_2, outs)
        num.write(f"Part_from_Chimeric_Read2:\t{count}\n")

# Example usage
process_sam_files('read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam', 'read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam', "read_1_toGenome_Chimeric.processed.sam", "read_2_toGenome_Chimeric.processed.sam", 'interaction_from_gapped_reads.sam')


commands = ['rm read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam', 'rm read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")


Command 'rm read_1_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam' executed successfully.
Command 'rm read_2_toGenome_Aligned.sortedByCoord.out.sort.uniq.sam' executed successfully.


In [17]:
# merge_interactions.pl

def read_strand_to_symbol(read_A_or_B, read_strand):
    if read_A_or_B == 1:
        if read_strand == 0 or read_strand == 256:
            return "Minus"
        elif read_strand == 16 or read_strand == 272:
            return "Plus"
        else:
            return "Ambiguous"
    elif read_A_or_B == 2:
        if read_strand == 0 or read_strand == 256:
            return "Plus"
        elif read_strand == 16 or read_strand == 272:
            return "Minus"
        else:
            return "Ambiguous"
    else:
        raise ValueError("Only 1 or 2 are allowed for read_A_or_B")

def main(num_of_interactions_from_part_list, paired_read_1_sam, paired_read_2_sam, gapped_sam, chimeric_1, chimeric_2, out_sam):
    part_from_AlignPair_readA_start = 1
    part_from_AlignPair_readA_end = None
    part_from_AlignPair_readB_start = None
    part_from_AlignPair_readB_end = None
    part_from_ChimericPair_readA_start = None
    part_from_ChimericPair_readA_end = None
    part_from_ChimericPair_readB_start = None
    part_from_ChimericPair_readB_end = None

    AlignPair_readA_head_segment = {}
    AlignPair_readB_head_segment = {}
    Chimeric_readA_junction_segment = {}
    Chimeric_readB_junction_segment = {}

    # Reading num_of_interactions_from_part_list
    with open(num_of_interactions_from_part_list) as nip:
        for line in nip:
            line = line.strip()
            if line.startswith("Part_from_Align_Read1:"):
                part_from_AlignPair_readA_end = int(line.split()[1])
                part_from_AlignPair_readB_start = part_from_AlignPair_readA_end + 1
            elif line.startswith("Part_from_Align_Read2:"):
                part_from_AlignPair_readB_end = part_from_AlignPair_readB_start - 1 + int(line.split()[1])
                part_from_ChimericPair_readA_start = part_from_AlignPair_readB_end + 1
            elif line.startswith("Part_from_Chimeric_Read1:"):
                part_from_ChimericPair_readA_end = part_from_ChimericPair_readA_start - 1 + int(line.split()[1])
                part_from_ChimericPair_readB_start = part_from_ChimericPair_readA_end + 1
            elif line.startswith("Part_from_Chimeric_Read2:"):
                part_from_ChimericPair_readB_end = part_from_ChimericPair_readB_start - 1 + int(line.split()[1])
            else:
                raise ValueError("Unexpected line in num_of_interactions_from_part_list")

    # Reading gapped_sam
    gapped_pair_id = 0
    with open(gapped_sam) as gs:
        for line in gs:
            if not line.startswith('@'):
                gapped_pair_id += 1
                frag_a = line
                frag_b = next(gs)
                id_a = frag_a.split()[0]
                id_b = frag_b.split()[0]
                if id_a != id_b:
                    raise ValueError("Wrong format")
                else:
                    sub_a = frag_a.split()
                    sub_b = frag_b.split()
                    strand_a = int(sub_a[1])
                    strand_b = int(sub_b[1])
                    loci_a = int(sub_a[3])
                    loci_b = int(sub_b[3])
                    strand_a = strand_a - 256 if strand_a > 255 else strand_a
                    strand_b = strand_b - 256 if strand_b > 255 else strand_b
                    if strand_a != strand_b:
                        print(frag_a, frag_b)
                        raise ValueError("Part segments but different strands")
                    
                    if part_from_AlignPair_readA_start <= gapped_pair_id <= part_from_AlignPair_readA_end:
                        if strand_a == 0:  # plus strand; save the left most
                            if sub_a[0] in AlignPair_readA_head_segment:
                                if loci_a < AlignPair_readA_head_segment[sub_a[0]][1]:
                                    AlignPair_readA_head_segment[sub_a[0]] = (frag_a, loci_a)
                            else:
                                AlignPair_readA_head_segment[sub_a[0]] = (frag_a, loci_a)
                        else:  # minus strand; save the right most
                            if sub_a[0] in AlignPair_readA_head_segment:
                                if loci_b > AlignPair_readA_head_segment[sub_a[0]][1]:
                                    AlignPair_readA_head_segment[sub_a[0]] = (frag_b, loci_b)
                            else:
                                AlignPair_readA_head_segment[sub_a[0]] = (frag_b, loci_b)
                    
                    elif part_from_AlignPair_readB_start <= gapped_pair_id <= part_from_AlignPair_readB_end:
                        if strand_a == 0:  # plus strand; save the left most
                            if sub_a[0] in AlignPair_readB_head_segment:
                                if loci_a < AlignPair_readB_head_segment[sub_a[0]][1]:
                                    AlignPair_readB_head_segment[sub_a[0]] = (frag_a, loci_a)
                            else:
                                AlignPair_readB_head_segment[sub_a[0]] = (frag_a, loci_a)
                        else:  # minus strand; save the right most
                            if sub_a[0] in AlignPair_readB_head_segment:
                                if loci_b > AlignPair_readB_head_segment[sub_a[0]][1]:
                                    AlignPair_readB_head_segment[sub_a[0]] = (frag_b, loci_b)
                            else:
                                AlignPair_readB_head_segment[sub_a[0]] = (frag_b, loci_b)
                    
                    elif part_from_ChimericPair_readA_start <= gapped_pair_id <= part_from_ChimericPair_readA_end:
                        if (strand_a == 0 and sub_a[0].endswith('Head')) or (strand_a == 16 and sub_a[0].endswith('Tail')):  # save the right most
                            if sub_a[0] in Chimeric_readA_junction_segment:
                                if loci_b > Chimeric_readA_junction_segment[sub_a[0]][1]:
                                    Chimeric_readA_junction_segment[sub_a[0]] = (frag_b, loci_b)
                            else:
                                Chimeric_readA_junction_segment[sub_a[0]] = (frag_b, loci_b)
                        elif (strand_a == 16 and sub_a[0].endswith('Head')) or (strand_a == 0 and sub_a[0].endswith('Tail')):  # save the left most
                            if sub_a[0] in Chimeric_readA_junction_segment:
                                if loci_a < Chimeric_readA_junction_segment[sub_a[0]][1]:
                                    Chimeric_readA_junction_segment[sub_a[0]] = (frag_a, loci_a)
                            else:
                                Chimeric_readA_junction_segment[sub_a[0]] = (frag_a, loci_a)
                    
                    elif part_from_ChimericPair_readB_start <= gapped_pair_id <= part_from_ChimericPair_readB_end:
                        if (strand_a == 0 and sub_a[0].endswith('Head')) or (strand_a == 16 and sub_a[0].endswith('Tail')):  # save the right most
                            if sub_a[0] in Chimeric_readB_junction_segment:
                                if loci_b > Chimeric_readB_junction_segment[sub_a[0]][1]:
                                    Chimeric_readB_junction_segment[sub_a[0]] = (frag_b, loci_b)
                            else:
                                Chimeric_readB_junction_segment[sub_a[0]] = (frag_b, loci_b)
                        elif (strand_a == 16 and sub_a[0].endswith('Head')) or (strand_a == 0 and sub_a[0].endswith('Tail')):  # save the left most
                            if sub_a[0] in Chimeric_readB_junction_segment:
                                if loci_a < Chimeric_readB_junction_segment[sub_a[0]][1]:
                                    Chimeric_readB_junction_segment[sub_a[0]] = (frag_a, loci_a)
                            else:
                                Chimeric_readB_junction_segment[sub_a[0]] = (frag_a, loci_a)
                    
                    else:
                        print(frag_a, frag_b)
                        raise ValueError("Source for this pair could not be found")

    # Reading paired_read_1_sam and paired_read_2_sam
    interaction_id = 0
    with open(paired_read_1_sam) as psa, open(paired_read_2_sam) as psb, open(out_sam, "w") as out_sam:
        for frag_a, frag_b in zip(psa, psb):
            if frag_a.startswith('@'):
                out_sam.write(frag_a) 
                
            if not frag_a.startswith('@'):
                id_a = frag_a.split()[0]
                id_b = frag_b.split()[0]   
                strand_a = int(frag_a.split()[1])
                strand_b = int(frag_b.split()[1])
                strand_a_symbol = read_strand_to_symbol(1, strand_a)
                strand_b_symbol = read_strand_to_symbol(2, strand_b)
                
                if id_a != id_b:
                    raise ValueError("Wrong format")
                else:
                    interaction_id += 1
                    if id_a in AlignPair_readA_head_segment and id_b in AlignPair_readB_head_segment:  # both
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_a_symbol}_{AlignPair_readA_head_segment[id_a][0]}")
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_b_symbol}_{AlignPair_readB_head_segment[id_b][0]}")
                    elif id_a in AlignPair_readA_head_segment and id_b not in AlignPair_readB_head_segment:
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_a_symbol}_{AlignPair_readA_head_segment[id_a][0]}")
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_b_symbol}_{frag_b}")
                    elif id_a not in AlignPair_readA_head_segment and id_b in AlignPair_readB_head_segment:
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_a_symbol}_{frag_a}")
                        out_sam.write(f"AlignPairSegment_{interaction_id}_{strand_b_symbol}_{AlignPair_readB_head_segment[id_b][0]}")
                    else:
                        out_sam.write(f"AlignPairWhole_{interaction_id}_{strand_a_symbol}_{frag_a}")
                        out_sam.write(f"AlignPairWhole_{interaction_id}_{strand_b_symbol}_{frag_b}")
    #processing gapped
    gapped_pair_id = 0
    with open(gapped_sam, "r") as GS, open("interaction_merge.sam", "a") as out_sam:
        for frag_a in GS:
            if frag_a.startswith('@'):
                continue
            else:
                frag_b = next(GS)
                id_a = frag_a.split()[0]
                id_b = frag_b.split()[0]
                if id_a != id_b:
                    raise ValueError("Wrong format")
                else:
                    gapped_pair_id += 1
                    interaction_id += 1
                    frag_a = frag_a.rstrip()
                    frag_b = frag_b.rstrip() #gapped
                    strand_a = int(frag_a.split()[1])
                    strand_a_symbol = None
                    
                    if gapped_pair_id >= part_from_AlignPair_readA_start and gapped_pair_id <= part_from_AlignPair_readA_end:
                        strand_a_symbol = read_strand_to_symbol(1, strand_a)
                        out_sam.write(f"Part_{interaction_id}_{strand_a_symbol}_{frag_a}\n") 
                        out_sam.write(f"Part_{interaction_id}_{strand_a_symbol}_{frag_b}\n")
                    elif gapped_pair_id >= part_from_AlignPair_readB_start and gapped_pair_id <= part_from_AlignPair_readB_end:
                        strand_a_symbol = read_strand_to_symbol(2, strand_a)
                        out_sam.write(f"Part_{interaction_id}_{strand_a_symbol}_{frag_a}\n")
                        out_sam.write(f"Part_{interaction_id}_{strand_a_symbol}_{frag_b}\n")
                    elif gapped_pair_id >= part_from_ChimericPair_readA_start and gapped_pair_id <= part_from_ChimericPair_readA_end:
                        continue
                    elif gapped_pair_id >= part_from_ChimericPair_readB_start and gapped_pair_id <= part_from_ChimericPair_readB_end:
                        continue
                    
                    
    # Reading chimeric_1 and chimeric_2
    with open(chimeric_1) as csa, open(chimeric_2) as csb, open("interaction_merge.sam", "a") as out_sam:
        for frag_a in csa:
            if not frag_a.startswith('@'):
                frag_b = next(csa)
                id_a = frag_a.split()[0]
                id_b = frag_b.split()[0]
                strand_a = int(frag_a.split()[1])
                strand_b = int(frag_b.split()[1]) #chimeric a
                strand_a_symbol = read_strand_to_symbol(1, strand_a)
                strand_b_symbol = read_strand_to_symbol(1, strand_b)
                interaction_id += 1
                
                if id_a in Chimeric_readA_junction_segment and id_b in Chimeric_readA_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{Chimeric_readA_junction_segment[id_a][0]}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{Chimeric_readA_junction_segment[id_b][0]}")
                elif id_a in Chimeric_readA_junction_segment and id_b not in Chimeric_readA_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{Chimeric_readA_junction_segment[id_a][0]}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{frag_b}")
                elif id_a not in Chimeric_readA_junction_segment and id_b in Chimeric_readA_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{frag_a}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{Chimeric_readA_junction_segment[id_b][0]}")
                else:
                    out_sam.write(f"ChimericWhole_{interaction_id}_{strand_a_symbol}_{frag_a}") 
                    out_sam.write(f"ChimericWhole_{interaction_id}_{strand_b_symbol}_{frag_b}")
                
        for frag_a in csb:
            if not frag_a.startswith('@'):
                frag_b = next(csb)
                
                id_a = frag_a.split()[0]
                id_b = frag_b.split()[0]
                strand_a = int(frag_a.split()[1])
                strand_b = int(frag_b.split()[1])
                strand_a_symbol = read_strand_to_symbol(2, strand_a)
                strand_b_symbol = read_strand_to_symbol(2, strand_b) #chimeric b
                interaction_id += 1
                if id_a in Chimeric_readB_junction_segment and id_b in Chimeric_readB_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{Chimeric_readB_junction_segment[id_a][0]}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{Chimeric_readB_junction_segment[id_b][0]}")
                elif id_a in Chimeric_readB_junction_segment and id_b not in Chimeric_readB_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{Chimeric_readB_junction_segment[id_a][0]}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{frag_b}")
                elif id_a not in Chimeric_readB_junction_segment and id_b in Chimeric_readB_junction_segment:
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_a_symbol}_{frag_a}")
                    out_sam.write(f"ChimericSegment_{interaction_id}_{strand_b_symbol}_{Chimeric_readB_junction_segment[id_b][0]}")
                else:
                    out_sam.write(f"ChimericWhole_{interaction_id}_{strand_a_symbol}_{frag_a}")
                    out_sam.write(f"ChimericWhole_{interaction_id}_{strand_b_symbol}_{frag_b}")

if __name__ == "__main__":
    
    num_of_interactions_from_part_list = "num_of_interactions_from_part.list"
    paired_read_1_sam = "interaction_from_pair_mapped_reads_1.sort.sam"
    paired_read_2_sam = "interaction_from_pair_mapped_reads_2.sort.sam"
    gapped_sam = "interaction_from_gapped_reads.sam"
    chimeric_1 = "read_1_toGenome_Chimeric.processed.sam"
    chimeric_2 = "read_2_toGenome_Chimeric.processed.sam"
    out_sam = "interaction_merge.sam"

    main(num_of_interactions_from_part_list, paired_read_1_sam, paired_read_2_sam, gapped_sam, chimeric_1, chimeric_2, "interaction_merge.sam")

# final output "interaction_merge.sam"


commands = ['rm num_of_interactions_from_part.list', 'rm interaction_from_pair_mapped_reads_1.sort.sam', "rm interaction_from_pair_mapped_reads_2.sort.sam", "rm interaction_from_gapped_reads.sam"]
#, "rm read_1_toGenome_Chimeric.processed.sam", "rm read_2_toGenome_Chimeric.processed.sam"
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")


Command 'rm num_of_interactions_from_part.list' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_1.sort.sam' executed successfully.
Command 'rm interaction_from_pair_mapped_reads_2.sort.sam' executed successfully.
Command 'rm interaction_from_gapped_reads.sam' executed successfully.


In [43]:
'''# count_link_for_each_interaction.pl
def main(paired_read_1_sam, paired_read_2_sam, gapped_count_before, chimeric_1, chimeric_2):
    pair_1 = read_count(paired_read_1_sam)
    pair_2 = read_count(paired_read_2_sam)
    gap_pair = part_count(gapped_count_before)
    C1 = read_count(chimeric_1)
    C2 = read_count(chimeric_2)

    if pair_1 != pair_2:
        raise ValueError("Pair reads not equal")
    else:
        print("pair\t", pair_1)

    print("gapped\t", gap_pair)
    print("C1\t", C1 / 2)
    print("C2\t", C2 / 2)


def part_count(file):
    part_num = 0
    with open(file, 'r') as f:
        for line in f:
            if line.startswith("Part_from_Align_Read"):
                part_num += int(line.split()[1])
    return part_num


def read_count(sam):
    reads_count = 0
    with open(sam, 'r') as f:
        for line in f:
            if not line.startswith('@'):
                reads_count += 1
    return reads_count


# Provide file paths as arguments to the main function
main("interaction_from_pair_mapped_reads_1.sort.sam",
     "interaction_from_pair_mapped_reads_2.sort.sam",
     "num_of_interactions_from_part.list",
     "read_1_toGenome_Chimeric.processed.sam",
     "read_2_toGenome_Chimeric.processed.sam")'''


'# count_link_for_each_interaction.pl\ndef main(paired_read_1_sam, paired_read_2_sam, gapped_count_before, chimeric_1, chimeric_2):\n    pair_1 = read_count(paired_read_1_sam)\n    pair_2 = read_count(paired_read_2_sam)\n    gap_pair = part_count(gapped_count_before)\n    C1 = read_count(chimeric_1)\n    C2 = read_count(chimeric_2)\n\n    if pair_1 != pair_2:\n        raise ValueError("Pair reads not equal")\n    else:\n        print("pair\t", pair_1)\n\n    print("gapped\t", gap_pair)\n    print("C1\t", C1 / 2)\n    print("C2\t", C2 / 2)\n\n\ndef part_count(file):\n    part_num = 0\n    with open(file, \'r\') as f:\n        for line in f:\n            if line.startswith("Part_from_Align_Read"):\n                part_num += int(line.split()[1])\n    return part_num\n\n\ndef read_count(sam):\n    reads_count = 0\n    with open(sam, \'r\') as f:\n        for line in f:\n            if not line.startswith(\'@\'):\n                reads_count += 1\n    return reads_count\n\n\n# Provide fil

In [44]:
# 183 extract intermolecular chimeric reads
#########
#########
#########
#########
#########
# separate_intra_inter_reads.pl
#identify chimeric reads, and separate them into two BED format files based on their strand information and chromosome positions

def parse_sam_file(sam_file, output_file_1, output_file_2):
    with open(sam_file, 'r') as sm, open(output_file_1, 'w') as out_file_1, open(output_file_2, 'w') as out_file_2:
        for line in sm:
            if line.startswith('@'):
                continue
            else:
                frag_a = line.strip()
                frag_b = next(sm).strip()

                sub_a = frag_a.split()
                sub_b = frag_b.split()

                id_a_info = sub_a[0].split('_')
                id_b_info = sub_b[0].split('_')

                if id_a_info[1] != id_b_info[1]:
                    print("Error: Fragments do not belong to the same pair.")

                strand_a = id_a_info[2]
                strand_b = id_b_info[2]

                chr_a = sub_a[2]
                loci_a = int(sub_a[3])
                cigar_a = sub_a[5]
                match_a_search = re.search(r'(\d+)M', cigar_a)
                match_a = int(match_a_search.group(1))
 

                chr_b = sub_b[2]
                loci_b = int(sub_b[3])
                cigar_b = sub_b[5]
                match_b_search = re.search(r'(\d+)M', cigar_b)
                match_b = int(match_b_search.group(1))


                if strand_a == "Plus":
                    out_file_1.write('\t'.join([chr_a, str(loci_a-1), str(loci_a+match_a-1), '_'.join(id_a_info[:2]), '255', '+']) + '\n')
                elif strand_a == "Minus":
                    out_file_1.write('\t'.join([chr_a, str(loci_a-1), str(loci_a+match_a-1), '_'.join(id_a_info[:2]), '255', '-']) + '\n')
                else:
                    print("Error: Wrong format.")

                if strand_b == "Plus":
                    out_file_2.write('\t'.join([chr_b, str(loci_b-1), str(loci_b+match_b-1), '_'.join(id_b_info[:2]), '255', '+']) + '\n')
                elif strand_b == "Minus":
                    out_file_2.write('\t'.join([chr_b, str(loci_b-1), str(loci_b+match_b-1), '_'.join(id_b_info[:2]), '255', '-']) + '\n')
                else:
                    print("Error: Wrong format.")


def main(sam_file, output_file_1, output_file_2):
    parse_sam_file(sam_file, output_file_1, output_file_2)

main("interaction_merge.sam", "read_1.bed", "read_2.bed") #### run this cell again if you change between gene/operon/genome .bed files  
#########
#########
#########


In [45]:
# used it to convert .gff3 file to a .bed with the same format they used

'''def gff3_to_bed(gff3_file, bed_file):
    with open(gff3_file, 'r') as gff3, open(bed_file, 'w') as bed:
        for line_num, line in enumerate(gff3, start=1):  # Add line number for debugging
            if line.strip() and not line.startswith('#'):
                fields = line.strip().split('\t')
                 
                
                if len(fields) >= 9:  # Check if the fields list has enough elements
                    seqid = fields[0]
                    start = int(fields[3]) - 0  # Convert 1-based start to 0-based start for BED format
                    end = int(fields[4])
                    feature_type = fields[2]
                    attributes_str = fields[8]
                    attributes = {}
                    for pair in attributes_str.split(';'):
                        if '=' in pair:
                            key, value = pair.split('=', 1)  # Split only once at the first occurrence of "="
                            attributes[key] = value
                    if 'ID' in attributes:
                        gene_id = attributes['ID']
                    else:
                        gene_id = seqid + ':' + str(start + 1) + '..' + str(end)
                    if 'Name' in attributes:
                        gene_name = attributes['Name']
                    else:
                        gene_name = gene_id
                    if 'strand' in fields[6]:
                        strand = fields[6]
                    else:
                        strand = '+'
                    
                    # Modify gene_id to remove everything after the '-' symbol
                    gene_id = gene_id.split('-')[0]
                    
                    bed_line = '\t'.join([seqid, str(start), str(end), gene_id, gene_name, strand]) + '\n'
                    bed.write(bed_line)
                else:
                    
                    print(f"Warning: Line {line_num} has fewer fields than expected: {line.strip()}")

# Example usage
gff3_to_bed('/mnt/c/Users/99alb/OneDrive/Desktop/data/Mg1655rmFstLine.gff.gff3', 'gene_region.bed')

#removed the first line with all the length of the genome'''


'def gff3_to_bed(gff3_file, bed_file):\n    with open(gff3_file, \'r\') as gff3, open(bed_file, \'w\') as bed:\n        for line_num, line in enumerate(gff3, start=1):  # Add line number for debugging\n            if line.strip() and not line.startswith(\'#\'):\n                fields = line.strip().split(\'\t\')\n                 \n                \n                if len(fields) >= 9:  # Check if the fields list has enough elements\n                    seqid = fields[0]\n                    start = int(fields[3]) - 0  # Convert 1-based start to 0-based start for BED format\n                    end = int(fields[4])\n                    feature_type = fields[2]\n                    attributes_str = fields[8]\n                    attributes = {}\n                    for pair in attributes_str.split(\';\'):\n                        if \'=\' in pair:\n                            key, value = pair.split(\'=\', 1)  # Split only once at the first occurrence of "="\n                          

In [46]:
#   OPERON .BED FILE
'''
input_file = '/mnt/c/Users/99alb/OneDrive/Desktop/data/all-transcription-units.txt'
output_file = 'operon_region.bed'

# Open the input and output files
with open(input_file, 'r') as infile, open(output_file, 'w') as outfile:
    # Skip the first line (header)
    next(infile)
    i=0
    # Process each line in the input file
    for line in infile:
        i+=1
        columns = line.split('\t')
        if len(columns)>4:
            try:
                start = int(columns[1])
                end = int(columns[2])
            except ValueError:
                print(f"Error: Non-integer value found in coordinates: {columns[1]}, {columns[2]}, {columns}")
                continue
            # Prepare the new columns according to the specified format
            chrom = 'NC_000913.3'
            name = 'op'
            score = str(i)
            strand = columns[3]
            
            # Write the output line to the .bed file
            if start < end:
                bed_line = '\t'.join([chrom, str(start), str(end), name, score, strand]) + '\n'
                outfile.write(bed_line)
            else:
                bed_line = '\t'.join([chrom, str(end), str(start), name, score, strand]) + '\n'
                outfile.write(bed_line)'''


'\ninput_file = \'/mnt/c/Users/99alb/OneDrive/Desktop/data/all-transcription-units.txt\'\noutput_file = \'operon_region.bed\'\n\n# Open the input and output files\nwith open(input_file, \'r\') as infile, open(output_file, \'w\') as outfile:\n    # Skip the first line (header)\n    next(infile)\n    i=0\n    # Process each line in the input file\n    for line in infile:\n        i+=1\n        columns = line.split(\'\t\')\n        if len(columns)>4:\n            try:\n                start = int(columns[1])\n                end = int(columns[2])\n            except ValueError:\n                print(f"Error: Non-integer value found in coordinates: {columns[1]}, {columns[2]}, {columns}")\n                continue\n            # Prepare the new columns according to the specified format\n            chrom = \'NC_000913.3\'\n            name = \'op\'\n            score = str(i)\n            strand = columns[3]\n            \n            # Write the output line to the .bed file\n            i

In [47]:

import pybedtools
pybedtools.helpers.set_bedtools_path("/usr/bin/")


def bedtools_intersect(whole_gene_bed, read_bed, output_bed):
    # Load the BED files as BedTool objects
    whole_gene_bedtool = pybedtools.BedTool(whole_gene_bed)
    read_bedtool = pybedtools.BedTool(read_bed)

    # Perform the intersect operation
    intersect_result = whole_gene_bedtool.intersect(read_bedtool, wa=True, wb=True)

    # Save the intersect result to a BED file
    intersect_result.saveas(output_bed)


#for operons
bedtools_intersect(f'{coordinate_file}', "read_1.bed", "gene_overlap_with_read1.bed")################################################################################################################################################################################################
bedtools_intersect(f'{coordinate_file}', "read_2.bed", "gene_overlap_with_read2.bed") ################################################################################################################################################################################################


In [48]:
#intra_pets_list.pl
#modified but hopefully the same

In [49]:
# shared ids between two files
# print it in a file
# for each check if first 5 entries are the same, if so = intra gene

def extract_ids(file_path):
    """Extract the 9th column (ID) from a given file."""
    ids = set()
    with open(file_path, 'r') as file:
        for line in file:
            columns = line.strip().split()
            if len(columns) >= 9:
                ids.add(columns[9])
    return ids

def find_shared_ids(file_a, file_b):
    """Find IDs that are shared between two files."""
    ids_a = extract_ids(file_a)
    ids_b = extract_ids(file_b)
    
    shared_ids = ids_a.intersection(ids_b)
    return shared_ids

def write_shared_ids_to_file(shared_ids, output_file):
    """Write the shared IDs to an output file."""
    with open(output_file, 'w') as file:
        for shared_id in shared_ids:
            file.write(shared_id + '\n')

# Specify the paths to your files
file_a = "gene_overlap_with_read1.bed"
file_b = "gene_overlap_with_read2.bed"
output_file = 'sharedID.txt'

# Find shared IDs
shared_ids = find_shared_ids(file_a, file_b)

# Write shared IDs to file
write_shared_ids_to_file(shared_ids, output_file)



In [50]:
#shared id file with features, but one at the time
def read_shared_ids(input_file):
    """Read shared IDs from a file."""
    shared_ids = set()
    with open(input_file, 'r') as file:
        for line in file:
            shared_ids.add(line.strip())
    return shared_ids

def extract_and_write_columns(file_a, shared_ids, output_file):
    """Extract specific columns from file A using shared IDs and write to output file."""
    with open(file_a, 'r') as file, open(output_file, 'w') as out_file:
        for line in file:
            columns = line.strip().split()
            if len(columns) >= 9 and columns[9] in shared_ids:
                selected_columns = [columns[9]] + columns[1:5]
                out_file.write('\t'.join(selected_columns) + '\n')
                
# Read shared IDs from file
shared_ids = read_shared_ids('sharedID.txt')

# Extract and write specific columns to new output file

extract_and_write_columns("gene_overlap_with_read1.bed", shared_ids, 'sharedID_r1.bed')
extract_and_write_columns("gene_overlap_with_read2.bed", shared_ids, 'sharedID_r2.bed')


commands = ["rm sharedID.txt"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")
   

Command 'rm sharedID.txt' executed successfully.


In [51]:
import subprocess

# List of commands to execute
commands = [
    "sort -k1,1 sharedID_r1.bed > sorted_sharedDr1.bed",
    "sort -k1,1 sharedID_r2.bed > sorted_sharedDr2.bed"
]

# Execute each command in sequence
for command in commands:
    try:
        subprocess.run(command, shell=True, check=True)
        print(f"Command '{command}' executed successfully.")
    except subprocess.CalledProcessError as e:
        print(f"An error occurred while executing '{command}': {e}")

commands = ["rm sharedID_r1.bed", "rm sharedID_r2.bed"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")
   


Command 'sort -k1,1 sharedID_r1.bed > sorted_sharedDr1.bed' executed successfully.
Command 'sort -k1,1 sharedID_r2.bed > sorted_sharedDr2.bed' executed successfully.
Command 'rm sharedID_r1.bed' executed successfully.
Command 'rm sharedID_r2.bed' executed successfully.


In [52]:
# divide the 2 files into 4 based on the suffixes, then singularly work with them 
#AlignPairWhole
#AlignPairSegment
#Part
#ChimericWhole

def divide_entries_by_prefix(input_path, output_dir):
    # Create output files for each prefix
    prefix_files = {}
    for prefix in ['AlignPairWhole_', 'AlignPairSegment_', 'Part_', 'ChimericWhole_']:
        prefix_files[prefix] = open(output_dir + '/' + prefix + 'entries.txt', 'w')

    # Read input file and divide entries by prefix
    with open(input_path, 'r') as input_file:
        for line in input_file:
            entry = line.strip()
            prefix = entry.split()[0].split('_')[0] + '_'
            if prefix in prefix_files:
                prefix_files[prefix].write(entry + '\n')

    # Close output files
    for file in prefix_files.values():
        file.close()

# Replace 'input.txt' and 'output_directory' with the paths to your input file and output directory
divide_entries_by_prefix('sorted_sharedDr1.bed', 'split_IDs1/')
divide_entries_by_prefix('sorted_sharedDr2.bed', 'split_IDs2/')

commands = ["rm sorted_sharedDr1.bed", "rm sorted_sharedDr2.bed"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm sorted_sharedDr1.bed' executed successfully.
Command 'rm sorted_sharedDr2.bed' executed successfully.


In [53]:

#check matching entries between the generated files

def find_matching_entries(file1_path, file2_path, output_path):
    # Read entries from file 1 into a set
    entries_file1 = set()
    with open(file1_path, 'r') as file1:
        for line in file1:
            entry = line.strip()
            entries_file1.add(entry)

    # Read entries from file 2 and compare with entries from file 1
    with open(file2_path, 'r') as file2, open(output_path, 'w') as output_file:
        for line in file2:
            entry = line.strip()
            if entry in entries_file1:
                output_file.write(line.split()[0] + '\n')

#

find_matching_entries('split_IDs1/AlignPairSegment_entries.txt', 'split_IDs2/AlignPairSegment_entries.txt', 'A_segmentIDs.txt')
find_matching_entries('split_IDs1/AlignPairWhole_entries.txt', 'split_IDs2/AlignPairWhole_entries.txt', 'A_whole.txt')
find_matching_entries('split_IDs1/ChimericWhole_entries.txt', 'split_IDs2/ChimericWhole_entries.txt', 'chimera.txt')
find_matching_entries('split_IDs1/Part_entries.txt', 'split_IDs2/Part_entries.txt', 'part.txt')

commands = ["rm split_IDs1/AlignPairSegment_entries.txt", "rm split_IDs2/AlignPairSegment_entries.txt", "rm split_IDs1/AlignPairWhole_entries.txt", "rm split_IDs2/AlignPairWhole_entries.txt", "rm split_IDs1/ChimericWhole_entries.txt", "rm split_IDs2/ChimericWhole_entries.txt", "rm split_IDs1/Part_entries.txt", "rm split_IDs2/Part_entries.txt"]
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm split_IDs1/AlignPairSegment_entries.txt' executed successfully.
Command 'rm split_IDs2/AlignPairSegment_entries.txt' executed successfully.
Command 'rm split_IDs1/AlignPairWhole_entries.txt' executed successfully.
Command 'rm split_IDs2/AlignPairWhole_entries.txt' executed successfully.
Command 'rm split_IDs1/ChimericWhole_entries.txt' executed successfully.
Command 'rm split_IDs2/ChimericWhole_entries.txt' executed successfully.
Command 'rm split_IDs1/Part_entries.txt' executed successfully.
Command 'rm split_IDs2/Part_entries.txt' executed successfully.


In [54]:
#concatenate the files to generate one .txt file

def concatenate_files(file_paths, output_path):
    with open(output_path, 'w') as output_file:
        for file_path in file_paths:
            with open(file_path, 'r') as input_file:
                # Read each line from the input file and write it to the output file
                for line in input_file:
                    output_file.write(line)

# Replace 'file1.txt', 'file2.txt', 'file3.txt', 'file4.txt' with the paths to your input files
input_files = ['A_segmentIDs.txt', 'A_whole.txt', 'chimera.txt','part.txt']
output_file = 'pets_in_same_gene.list'

concatenate_files(input_files, output_file)
#remove them afterwards

commands = ['rm A_segmentIDs.txt', 'rm A_whole.txt', 'rm chimera.txt','rm part.txt']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm A_segmentIDs.txt' executed successfully.
Command 'rm A_whole.txt' executed successfully.
Command 'rm chimera.txt' executed successfully.
Command 'rm part.txt' executed successfully.


In [55]:
# separate_intra_inter_pets.pl

# inputs: interaction_merge.sam and pets_in_same_gene.list 

def process_sam_files(contact_sam, list_file):
    # Create output file names
    output_intra_sam = contact_sam.replace("sam", "intraMolecular.sam")
    output_inter_sam = contact_sam.replace("sam", "interMolecular.sam")

    # Read the list file and store it in a set
    intra_list = set()
    with open(list_file, 'r') as lst:
        for line in lst:
            intra_list.add(line.strip())

    # Open output files
    with open(output_intra_sam, 'w') as intra, open(output_inter_sam, 'w') as inter, open(contact_sam, 'r') as sm:
        while True:
            frag_a = sm.readline()
            if not frag_a:
                break
            if frag_a.startswith('@'):
                intra.write(frag_a)
                inter.write(frag_a)
                continue

            frag_b = sm.readline()
            if not frag_b:
                break

            sub_a = frag_a.split()
            sub_b = frag_b.split()

            id_a_info = sub_a[0].split('_')
            id_b_info = sub_b[0].split('_')

            if id_a_info[1] != id_b_info[1]:  # Ensure they belong to the same pair
                print(frag_a, frag_b)
                raise ValueError("Did not belong to the same pair")

            key = f"{id_a_info[0]}_{id_a_info[1]}"
            frag_a = frag_a.rstrip()
            frag_b = frag_b.rstrip()

            if key in intra_list:
                intra.write(f"{frag_a}\n{frag_b}\n")
            else:
                inter.write(f"{frag_a}\n{frag_b}\n")

# Example usage


process_sam_files("interaction_merge.sam", "pets_in_same_gene.list")

# output interaction_merge.interMolecular.sam and interaction_merge.intraMolecular.sam 


commands = ['rm pets_in_same_gene.list'] # 'rm interaction_merge.sam', 
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm pets_in_same_gene.list' executed successfully.


In [56]:
#from_sam_to_pair_reads_bed.pl
# input = interaction_merge.interMolecular.sam

"""def process_sam_file(sam_file):
    with open("read_1.bed", "w") as out_a, open("read_2.bed", "w") as out_b, open(sam_file, "r") as sm:
        for frag_a in sm:
            if frag_a.startswith('@'):
                continue

            frag_b = next(sm, None)
            if frag_b is None:
                break

            sub_a = frag_a.split()
            sub_b = frag_b.split()

            id_a_info = sub_a[0].split('_')
            id_b_info = sub_b[0].split('_')
            strand_a = id_a_info[2]
            strand_b = id_b_info[2]

            if id_a_info[1] != id_b_info[1]:  # Ensure they belong to the same pair
                print(frag_a, frag_b)
                raise ValueError("Did not belong to the same pair")

            chr_a = sub_a[2]
            loci_a = int(sub_a[3])
            match_a = int(sub_a[5].split('M')[0].split('S')[0].split('N')[0].split('I')[0])

            chr_b = sub_b[2]
            loci_b = int(sub_b[3])
            match_b = int(sub_b[5].split('M')[0].split('S')[0].split('N')[0].split('I')[0])

            if strand_a == "Plus":
                out_a.write(f"{chr_a}\t{loci_a - 1}\t{loci_a + match_a - 1}\t{id_a_info[0]}_{id_a_info[1]}\t255\t+\n")
            elif strand_a == "Minus":
                out_a.write(f"{chr_a}\t{loci_a - 1}\t{loci_a + match_a - 1}\t{id_a_info[0]}_{id_a_info[1]}\t255\t-\n")
            else:
                raise ValueError("Wrong format")

            if strand_b == "Plus":
                out_b.write(f"{chr_b}\t{loci_b - 1}\t{loci_b + match_b - 1}\t{id_b_info[0]}_{id_b_info[1]}\t255\t+\n")
            elif strand_b == "Minus":
                out_b.write(f"{chr_b}\t{loci_b - 1}\t{loci_b + match_b - 1}\t{id_b_info[0]}_{id_b_info[1]}\t255\t-\n")
            else:
                raise ValueError("Wrong format")


process_sam_file('interaction_merge.interMolecular.sam')"""

#output read_1.bed and 2 anew

In [57]:
#21

"""import pybedtools
pybedtools.helpers.set_bedtools_path("/usr/bin/")


def bedtools_intersect(whole_gene_bed, read_bed, output_bed):
    # Load the BED files as BedTool objects
    whole_gene_bedtool = pybedtools.BedTool(whole_gene_bed)
    read_bedtool = pybedtools.BedTool(read_bed)

    # Perform the intersect operation
    intersect_result = whole_gene_bedtool.intersect(read_bedtool, wa=True, wb=True)

    # Save the intersect result to a BED file
    intersect_result.saveas(output_bed)

#operon_ or gene_region.bed based on thw assignment
bedtools_intersect(f'{coordinate_file}', "read_1.bed", "gene_overlap_with_read1.bed") ################################################################################################################################################
bedtools_intersect(f'{coordinate_file}', "read_2.bed", "gene_overlap_with_read2.bed")################################################################################################################################################


commands = ['rm read_1.bed', 'rm read_2.bed']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")"""


Command 'rm read_1.bed' executed successfully.
Command 'rm read_2.bed' executed successfully.


In [58]:
# input: interaction_merge.interMolecular.sam , gene_overlap_with_read1.bed , gene_overlap_with_read2.bed

"""def process_interaction_sam(interaction_sam, gene_read_1, gene_read_2):
    # Read gene overlap BED files
    read_in_gene = set()
    with open(gene_read_1, 'r') as ina, open(gene_read_2, 'r') as inb:
        for line in ina:
            read_in_gene.add(line.split()[9]) # AlignPairWhole_53417 for example
        for line in inb:
            read_in_gene.add(line.split()[9])

    # Define output file names
    with_sam = interaction_sam.replace(".sam", ".withGene.sam")
    without_sam = interaction_sam.replace(".sam", ".withoutGene.sam")

    # Open output files
    with open(with_sam, 'w') as withg, open(without_sam, 'w') as withoutg, open(interaction_sam, 'r') as sm:
        for frag_a in sm:
            if frag_a.startswith('@'):
                withg.write(frag_a)
                withoutg.write(frag_a)
                continue

            frag_b = next(sm, None)
            if not frag_b:
                break

            sub_a = frag_a.split()
            sub_b = frag_b.split()
            id_a_info = sub_a[0].split('_')
            id_b_info = sub_b[0].split('_')

            if id_a_info[1] != id_b_info[1]:  # Ensure they belong to the same pair
                print(frag_a, frag_b)
                raise ValueError("Did not belong to the same pair")

            if id_a_info[0] + "_" + id_a_info[1] in read_in_gene:
                withg.write(frag_a)
                withg.write(frag_b)
            else:
                withoutg.write(frag_a)
                withoutg.write(frag_b)

# Example usage
process_interaction_sam('interaction_merge.interMolecular.sam' , 'gene_overlap_with_read1.bed' , 'gene_overlap_with_read2.bed')

#output interaction_merge.interMolecular.withGene.sam and interaction_merge.interMolecular.withoutGene.sam 
#not used?

commands = ['rm interaction_merge.interMolecular.sam', 'rm gene_overlap_with_read1.bed' , 'rm gene_overlap_with_read2.bed']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")"""

Command 'rm interaction_merge.interMolecular.sam' executed successfully.
Command 'rm gene_overlap_with_read1.bed' executed successfully.
Command 'rm gene_overlap_with_read2.bed' executed successfully.


In [59]:
# 184
# categorize intramolecular pairwise tags as either chimeric or singleton 

# need an integer number used as 'minimum_fragment_size', gapped reads resulting from RNA splicing and pair-end reads with a transcriptomic span shorter than the number are classified as singletons

#input is INTRA
# input: interaction_merge.intraMolecular.sam // minimum_fragment_size // gene_region.bed // exon_junction.bedpe

In [60]:
#creat_gapped_and_Align_pair_bed.pl
import re
def process_sam_file(sam_file, minimum_fragment_len):
    # Define output file names
    output_alignpair_A = re.sub(r'sam$', 'Alignpair_read1.bed', sam_file)
    output_alignpair_B = re.sub(r'sam$', 'Alignpair_read2.bed', sam_file)
    output_part = re.sub(r'sam$', 'gapped.bed', sam_file)

    # Open the output files
    with open(output_alignpair_A, 'w') as apa, \
         open(output_alignpair_B, 'w') as apb, \
         open(output_part, 'w') as pt, \
         open(sam_file, 'r') as sm:

        # Iterate through the SAM file
        while True:
            frag_a = sm.readline()
            if not frag_a:
                break
            if frag_a.startswith('@'):
                continue
            frag_b = sm.readline()
            if not frag_b:
                break

            sub_a = frag_a.split()
            sub_b = frag_b.split()

            id_a_info = sub_a[0].split('_')
            id_b_info = sub_b[0].split('_')

            if id_a_info[1] != id_a_info[1]:  # same pair check
                print(frag_a, frag_b)
                raise ValueError("Did not belong to the same pair")
            else:  # same read name
                chr_a = sub_a[2]
                loci_a = int(sub_a[3])
                cigar_a = sub_a[5]

                chr_b = sub_b[2]
                loci_b = int(sub_b[3])
                cigar_b = sub_b[5]

                if sub_a[0].startswith('AlignPair'):
                    match_a_search = re.search(r'(\d+)M', cigar_a)
                    match_b_search = re.search(r'(\d+)M', cigar_b)
                    
                    if match_a_search and match_b_search:
                        match_a = int(match_a_search.group(1))
                        match_b = int(match_b_search.group(1))

                        if id_a_info[2] == id_b_info[2]:  # same strand
                            if id_a_info[2] == "Plus":
                                fragment_len = loci_a + match_a - loci_b
                                if fragment_len > minimum_fragment_len:
                                    apa.write(f"{chr_a}\t{loci_a-1}\t{loci_a+match_a-1}\t{sub_a[0]}\t255\t+\n")
                                    apb.write(f"{chr_b}\t{loci_b-1}\t{loci_b+match_b-1}\t{sub_b[0]}\t255\t+\n")
                            elif id_a_info[2] == "Minus":
                                fragment_len = loci_b + match_b - loci_a
                                if fragment_len > minimum_fragment_len:
                                    apa.write(f"{chr_a}\t{loci_a-1}\t{loci_a+match_a-1}\t{sub_a[0]}\t255\t-\n")
                                    apb.write(f"{chr_b}\t{loci_b-1}\t{loci_b+match_b-1}\t{sub_b[0]}\t255\t-\n")
                
                elif sub_a[0].startswith('Part'):
                    match_a_search = re.search(r'(\d+)M', cigar_a)
                    match_b_search = re.search(r'(\d+)M', cigar_b)
                    
                        
                    if match_a_search and match_b_search:
                        match_a = int(match_a_search.group(1))
                        match_b = int(match_b_search.group(1))
                        pt.write(f"{chr_a}\t{loci_a+match_a-5}\t{loci_a+match_a+5}\t")
                        pt.write(f"{chr_b}\t{loci_b-5}\t{loci_b+5}\t")
                        pt.write(f"{sub_a[0]}\t60\t+\t+\n")
                
                else:
                    # Chimeric reads; all classified as chimeric
                    pass


# Example usage:
process_sam_file('interaction_merge.intraMolecular.sam', min_frag_size) #gapped reads resulting from RNA splicing and pair-end reads with transcriptomic span shorter than the NUMBER are classified as singletons

#output interaction_merge.intraMolecular.Alignpair_read1.bed // interaction_merge.intraMolecular.Alignpair_read2.bed // interaction_merge.intraMolecular.gapped.bed

In [61]:
import pybedtools
import subprocess
pybedtools.helpers.set_bedtools_path("/usr/bin/")


def bedtools_intersect(whole_gene_bed, read_bed, output_bed):
    # Load the BED files as BedTool objects
    whole_gene_bedtool = pybedtools.BedTool(whole_gene_bed)
    read_bedtool = pybedtools.BedTool(read_bed)

    # Perform the intersect operation
    intersect_result = whole_gene_bedtool.intersect(read_bedtool, wa=True, wb=True, s=True)

    # Save the intersect result to a BED file
    intersect_result.saveas(output_bed)

#operon_ or gene_region.bed based on assignment
bedtools_intersect(f'{coordinate_file}', "interaction_merge.intraMolecular.Alignpair_read1.bed", "element_overlap_with_read1.bed") #################################################### #################################################### ####################################################
bedtools_intersect(f'{coordinate_file}', "interaction_merge.intraMolecular.Alignpair_read2.bed", "element_overlap_with_read2.bed") ####################################################  #################################################### ####################################################

commands = ['rm interaction_merge.intraMolecular.Alignpair_read1.bed', 'rm interaction_merge.intraMolecular.Alignpair_read2.bed']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm interaction_merge.intraMolecular.Alignpair_read1.bed' executed successfully.
Command 'rm interaction_merge.intraMolecular.Alignpair_read2.bed' executed successfully.


In [62]:
#generate bedpe file
def bed_to_bedpe(bed_file, bedpe_file):
    
    with open(bed_file, 'r') as infile, open(bedpe_file, 'w') as outfile:
        for line in infile:
            if line.strip():  # Skip empty lines
                fields = line.strip().split('\t')
                chrom1 = fields[0]
                start1 = fields[1]
                end1 = fields[2]
                chrom2 = fields[3]
                start2 = fields[4]
                end2 = fields[5]
                string = fields[6]
                num = fields[7]
                sym1 = fields[8]
                sym2 =fields[9]
                
                # Duplicate the entry for .bedpe format
                bedpe_line = f"{chrom1}\t{start1}\t{end1}\t{chrom2}\t{start2}\t{end2}\t{string}\t{num}\t{sym1}\t{sym2}\n"
                outfile.write(bedpe_line)

bed_to_bedpe('interaction_merge.intraMolecular.gapped.bed', 'interaction_merge.intraMolecular.gapped.bedpe')

commands = ['rm interaction_merge.intraMolecular.gapped.bed']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm interaction_merge.intraMolecular.gapped.bed' executed successfully.


In [63]:
#generate bedpe file
def bed_to_bedpe(bed_file, bedpe_file):
    with open(bed_file, 'r') as infile, open(bedpe_file, 'w') as outfile:
        for line in infile:
            if line.strip():  # Skip empty lines
                fields = line.strip().split('\t')
                chrom = fields[0]
                start = fields[1]
                end = fields[2]
                mid = round((int(start) + int(end))/2)
                mid_1 = int(mid) + 1
                
                
                type = fields[3]
                name = fields[4]
                symbol = fields[5]
                string = f"{type}_{name}"
                # Duplicate the entry for .bedpe format
                bedpe_line = f"{chrom}\t{start}\t{mid}\t{chrom}\t{mid_1}\t{end}\t{string}\t{60}\t{symbol}\t{symbol}\n"
                outfile.write(bedpe_line)

# operon_ or gene_region.bed based on assignment
bed_to_bedpe(f'{coordinate_file}', 'gene_region_nonexon.bedpe')  #################################################### #################################################### ####################################################


In [64]:
#20   print "bedtools pairtopair -a $prefix.gapped.bed -b $exon_junction_bedpe -is > gapped_reads_overlapped_with_exon_junction.list\n";

import pybedtools

def pairtopair_bedtools(a_file, b_file, output_file):
    # Create BedTool objects
    a = pybedtools.BedTool(a_file)
    b = pybedtools.BedTool(b_file)
    
    # Perform the pairtopair operation with -is (same strand)
    result = a.pairtopair(b)
    
    # Save the result to the output file
    result.saveas(output_file)

# Example usage:

pairtopair_bedtools(
    'interaction_merge.intraMolecular.gapped.bedpe',
    'gene_region_nonexon.bedpe', 
    'gapped_reads_overlapped_with_exon_junction.list')

commands = ['rm interaction_merge.intraMolecular.gapped.bedpe']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm interaction_merge.intraMolecular.gapped.bedpe' executed successfully.


In [65]:
# distance_in_mature_trans.pl
def read_gene_element_bed(gene_element_bed):
    trans_element_loci = {}
    trans_strand = {}
    trans_type = {}
    
    with open(gene_element_bed, 'r') as file:
        for line in file:
            fields = line.strip().split()
            trans_id = fields[4]
            trans_strand.setdefault(trans_id, {})[fields[-1]] = 1
            trans_element_loci.setdefault(trans_id, []).append(fields[:4])
            if fields[4].startswith('PC'):
                trans_type[trans_id] = "ProteinCoding"
            elif fields[4].startswith('NC'):
                trans_type[trans_id] = "NonCoding"
    
    return trans_element_loci, trans_strand, trans_type #################################### transtype is empty !!!!!

def read_gene_read(gene_read_file):
    element_read = {}
    with open(gene_read_file, 'r') as file:
        for line in file:
            fields = line.strip().split()
            trans_id = fields[4]
            read_info = "\t".join(fields[6:])
            element_read.setdefault(trans_id, []).append(read_info)
    
    return element_read


def fragment_len_in_mature(left_read, right_read, trans, trans_element_loci, trans_strand):
    left_read_info = left_read.split()
    right_read_info = right_read.split()

    trans_element_loci = trans_element_loci[trans]

    trans_len = 0
    left_read_to_tss = 0
    right_read_to_tss = 0
    left_to_right = 0

    raw_trans_element = trans_element_loci

    if trans_strand[trans].get("+") and not trans_strand[trans].get("-"):
        #print(left_read_info)
        left_read_start = (int(left_read_info[1]) + int(left_read_info[2])) // 2
        right_read_start = int(right_read_info[2])
        left_to_right = right_read_start - left_read_start
        trans_element = sorted(raw_trans_element, key=lambda x: int(x[1]))  # sort by region start; from min to max
        for trans_item in trans_element:
            if "Intron" in trans_item[3]:
                continue
            trans_len += int(trans_item[2]) - int(trans_item[1])

        left_element_index = None
        for index, trans_item in enumerate(trans_element):
            if int(trans_item[2]) < left_read_start:
                if "Intron" in trans_item[3]:
                    continue
                left_read_to_tss += int(trans_item[2]) - int(trans_item[1])
            elif int(trans_item[1]) <= left_read_start <= int(trans_item[2]):
                left_read_to_tss += left_read_start - int(trans_item[1])
                left_element_index = index
                break

        for trans_item in trans_element:
            if int(trans_item[2]) < right_read_start:
                if "Intron" in trans_item[3]:
                    if left_element_index is not None and left_element_index <= index:
                        right_read_to_tss += int(trans_item[2]) - int(trans_item[1])
                    continue
                else:
                    right_read_to_tss += int(trans_item[2]) - int(trans_item[1])
            elif int(trans_item[1]) <= right_read_start <= int(trans_item[2]):
                right_read_to_tss += right_read_start - int(trans_item[1])
                break

    elif not trans_strand[trans].get("+") and trans_strand[trans].get("-"):
        left_read_start = (int(left_read_info[1]) + int(left_read_info[2])) // 2
        right_read_start = int(right_read_info[1])
        left_to_right = left_read_start - right_read_start
        trans_element = sorted(raw_trans_element, key=lambda x: int(x[1]), reverse=True)  # sort by region start; from max to min
        for trans_item in trans_element:
            if "Intron" in trans_item[3]:
                continue
            trans_len += int(trans_item[2]) - int(trans_item[1])

        left_element_index = None
        for index, trans_item in enumerate(trans_element):
            if int(trans_item[1]) > left_read_start:
                if "Intron" in trans_item[3]:
                    continue
                left_read_to_tss += int(trans_item[2]) - int(trans_item[1])
            elif int(trans_item[1]) <= left_read_start <= int(trans_item[2]):
                left_read_to_tss += int(trans_item[2]) - left_read_start
                left_element_index = index
                break

        for trans_item in trans_element:
            if int(trans_item[1]) > right_read_start:
                if "Intron" in trans_item[3]:
                    if left_element_index is not None and left_element_index <= index:
                        right_read_to_tss += int(trans_item[2]) - int(trans_item[1])
                    continue
                else:
                    right_read_to_tss += int(trans_item[2]) - int(trans_item[1])
            elif int(trans_item[1]) <= right_read_start <= int(trans_item[2]):
                right_read_to_tss += right_read_start - int(trans_item[1])
                break

    else:
        raise ValueError(f"Wrong trans strand for {trans}")

    fragment_len = right_read_to_tss - left_read_to_tss
    return left_to_right, fragment_len

def calculate_fragment_length(gene_element_bed, gene_read_1, gene_read_2, output_file):
    trans_element_loci, trans_strand, _ = read_gene_element_bed(gene_element_bed)
    element_read_A = read_gene_read(gene_read_1)
    element_read_B = read_gene_read(gene_read_2)
    
    min_fragment_trans = {}
    min_fragment_len = {}
    distance_in_preRNA = {}
    
    for trans in element_read_A:
        if trans in element_read_B:
            reads_A_set = element_read_A[trans]
            reads_B_set = element_read_B[trans]
            common_id = {}
            for tmp_read_a in reads_A_set:
                tmp_read_id = tmp_read_a.split()[3]
                common_id[tmp_read_id] = {'1': tmp_read_a}
            for tmp_read_b in reads_B_set:
                tmp_read_id = tmp_read_b.split()[3]
                common_id.setdefault(tmp_read_id, {}).update({'2': tmp_read_b})
            
            for i in common_id:
                if i in min_fragment_len and min_fragment_len[i] <= 300:
                    continue
                if '1' not in common_id[i] or '2' not in common_id[i]:
                    continue
                
                left_read = common_id[i]['2']
                right_read = common_id[i]['1']
                pre_len, frag_len = fragment_len_in_mature(left_read, right_read, trans, trans_element_loci, trans_strand)
                distance_in_preRNA[i] = pre_len
                if i in min_fragment_len:
                    if frag_len < min_fragment_len[i]:
                        min_fragment_len[i] = frag_len
                        min_fragment_trans[i] = trans
                else:
                    min_fragment_len[i] = frag_len
                    min_fragment_trans[i] = trans
    
    with open(output_file, 'w') as file:
        for i in min_fragment_len:
            file.write(f"{i}\t{distance_in_preRNA.get(i, '')}\t{min_fragment_len[i]}\t{min_fragment_trans[i]}\n")

#operon or gene_region.bed based on assignment
input_gene_element_bed = coordinate_file #################################################### #################################################### #################################################### ####################################################
input_gene_read_1 = "element_overlap_with_read1.bed" 
input_gene_read_2 = "element_overlap_with_read2.bed" 
output_file = "pairreads_distance_in_mature_trans.list"



calculate_fragment_length(input_gene_element_bed, input_gene_read_1, input_gene_read_2, output_file)


commands = ['rm element_overlap_with_read1.bed','rm element_overlap_with_read2.bed']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")


Command 'rm element_overlap_with_read1.bed' executed successfully.
Command 'rm element_overlap_with_read2.bed' executed successfully.


In [66]:
# split_intra_to_Normal_Chimeric.pl

def classify_reads(
    in_sam, 
    junction_reads, 
    pairreads_distance_in_mature, 
    minimal_fragment_len_for_pair
):
    # Load the bad_read_gap_pair dictionary
    bad_read_gap_pair = {}
    '''with open(junction_reads, 'r') as junc_file:                       ############## i commented this to make empty list
        for line in junc_file:
            sub = line.strip().split()
            bad_read_gap_pair[sub[6]] = 1'''


    # Load the close_reads_in_mature dictionary
    close_reads_in_mature = {}
    with open(pairreads_distance_in_mature, 'r') as pdm_file:
        for line in pdm_file:
            sub = line.strip().split()
            close_reads_in_mature[sub[0]] = int(sub[2])

    # Define output file names
    normal_sam = in_sam.replace('sam', 'Singleton.sam')                   
    chimeric_sam = in_sam.replace('sam', 'Chimeric.sam')
    dropped_sam = in_sam.replace('sam', 'dropped.sam')

    # Process the input SAM file and classify reads
    with open(in_sam, 'r') as sm_file, \
            open(normal_sam, 'w') as outn, \
            open(chimeric_sam, 'w') as outc, \
            open(dropped_sam, 'w') as outd, \
            open('class_of_AlignPair.log', 'w') as log_file:
        
        while True:
            frag_a = sm_file.readline()
            if not frag_a:
                break
            if frag_a.startswith('@'):
                #outn.write(frag_a)
                outc.write(frag_a)
                #outd.write(frag_a)
            else:
                frag_b = sm_file.readline()
                if not frag_b:
                    break

                sub_a = frag_a.strip().split()
                sub_b = frag_b.strip().split()
                id_a_info = sub_a[0].split('_')
                id_b_info = sub_b[0].split('_')
                strand_a = id_a_info[2]
                strand_b = id_b_info[2]
                if id_a_info[1] != id_b_info[1]:  # same pair
                    print(frag_a, frag_b)
                    raise ValueError("did not belong to the same pair")

                chr_a = sub_a[2]
                loci_a = int(sub_a[3])
                cigar_a = sub_a[5]

                chr_b = sub_b[2]
                loci_b = int(sub_b[3])
                cigar_b = sub_b[5]

                if "AlignPair" in sub_a[0]:  # pair
                    match_a = int(re.search(r'(\d+)M', cigar_a).group(1))
                    match_b = int(re.search(r'(\d+)M', cigar_b).group(1))

                    if strand_a == strand_b:
                        if strand_a == "Plus":
                            fragment_len = loci_a + match_a - loci_b
                            if fragment_len < 0:  # conflict direction
                                outc.write(frag_a)
                                outc.write(frag_b)
                                #log_file.write(f"{sub_a[0]}\t3'ReadsAt5'\tChimeric\n")
                            #elif fragment_len <= minimal_fragment_len_for_pair:  # smaller than minimal; even in pre-RNA
                                #outn.write(frag_a)
                                #outn.write(frag_b)
                                #log_file.write(f"{sub_a[0]}\tFragmentShorterThan{minimal_fragment_len_for_pair}inPre-RNA\tNormal\n")
                            else:
                                if sub_a[0] in close_reads_in_mature:
                                    if close_reads_in_mature[sub_a[0]] <= minimal_fragment_len_for_pair:  # closer than minimal; in mature RNA
                                        usless_variable=0
                                        #outn.write(frag_a)
                                        #outn.write(frag_b)
                                        #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAButShorterThan{minimal_fragment_len_for_pair}inMatureRNA\tNormal\n")
                                    else:  # farther than minimal; in mature RNA
                                        outc.write(frag_a)
                                        outc.write(frag_b)
                                        #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAAndLongerThan{minimal_fragment_len_for_pair}inMatureRNA\tChimeric\n")
                                #else:
                                    #outd.write(">no_transcripts_available\n")
                                    #outd.write(frag_a)
                                    #outd.write(frag_b)
                                    #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAButNoAvailableTranscripts\tDropped\n")
                        elif strand_a == "Minus":
                            fragment_len = loci_b + match_b - loci_a
                            if fragment_len < 0:  # conflict direction
                                outc.write(frag_a)
                                outc.write(frag_b)
                                #log_file.write(f"{sub_a[0]}\t3'ReadsAt5'\tChimeric\n")
                            elif fragment_len <= minimal_fragment_len_for_pair:  # smaller than minimal; even in pre-RNA
                                usless_variable=0
                                #outn.write(frag_a)
                                #outn.write(frag_b)
                                #log_file.write(f"{sub_a[0]}\tFragmentShorterThan{minimal_fragment_len_for_pair}inPre-RNA\tNormal\n")
                            else:
                                if sub_a[0] in close_reads_in_mature:
                                    if close_reads_in_mature[sub_a[0]] <= minimal_fragment_len_for_pair:  # closer than minimal; in mature RNA
                                        usless_variable=0
                                        #outn.write(frag_a)
                                        #outn.write(frag_b)
                                        #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAButShorterThan{minimal_fragment_len_for_pair}inMatureRNA\tNormal\n")
                                    else:  # farther than minimal in mature RNA
                                        outc.write(frag_a)
                                        outc.write(frag_b)
                                        #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAAndLongerThan{minimal_fragment_len_for_pair}inMatureRNA\tChimeric\n")
                                else:
                                    usless_variable=0
                                    #outd.write(">no_transcripts_available\n")
                                    #outd.write(frag_a)
                                    #outd.write(frag_b)
                                    #log_file.write(f"{sub_a[0]}\tFragmentLongerThan{minimal_fragment_len_for_pair}inPre-RNAButNoAvailableTranscripts\tDropped\n")
                    else:  # same fragment but different strand; may be result from intergene interaction
                        usless_variable=0
                        #outd.write(">maybe_intergene\n")
                        #outd.write(frag_a)
                        #outd.write(frag_b)
                        #log_file.write(f"{sub_a[0]}\tSameFragment_DifferentStrand_MayBeInterGene\tDropped\n")
                elif "Chimeric" in sub_a[0]:  # chimeric reads: classified as RNA structure
                    outc.write(frag_a)
                    outc.write(frag_b)
                    #log_file.write(f"{sub_a[0]}\tChimericFragment\tChimeric\n")
                elif "Part" in sub_a[0]:
                    if sub_a[0] in bad_read_gap_pair:  # gapped reads overlap with exon junction: classified as Normal RNA-seq
                        usless_variable=0
                        #outn.write(frag_a)             # bad_read_gap_pair is empty because no splicing junction!!!!!
                        #outn.write(frag_b)
                        #log_file.write(f"{sub_a[0]}\tPartSegmentOnExonJunction\tNormal\n")
                    else:  # gapped reads do not overlap with exon junction: classified as RNA structure
                        usless_variable=0
                        outc.write(frag_a)
                        outc.write(frag_b)
                        #log_file.write(f"{sub_a[0]}\tPartSegmentAwayFromExonJunction\tChimeric\n")
                else:
                    print(frag_a, frag_b)
                    raise ValueError(f"wrong read id: {sub_a[0]}")


# Example call to the function
in_sam = 'interaction_merge.intraMolecular.sam'
junction_reads = 'gapped_reads_overlapped_with_exon_junction.list'
pairreads_distance_in_mature = "pairreads_distance_in_mature_trans.list"
minimal_fragment_len_for_pair = min_frag_len_pair ####################################################################################################################################################################


classify_reads(in_sam, junction_reads, pairreads_distance_in_mature, minimal_fragment_len_for_pair) # minimal_fragment_len_for_pair(must be larger than num used in creat_gapped_and_Align_pair_bed.pl!!!!)

#output 
#interaction_merge.intraMolecular.Chimeric.sam
#interaction_merge.intraMolecular.Singleton.sam
#interaction_merge.intraMolecular.dropped.sam

commands = ['rm gapped_reads_overlapped_with_exon_junction.list']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm gapped_reads_overlapped_with_exon_junction.list' executed successfully.


In [67]:
# 185
# 4 inputs:
#fragment_number_cutoff 
#connection_score_cutoff
#tmp.prefix
#rep1.intramolecular.chimeric.sam = interaction_merge.intraMolecular.Chimeric.sam
# can put more replicas like the last input



In [68]:
# 1.cluster ##############################################################################################################################################################################################################
# from_sam_to_bedOfPair.pl

def sam_to_bedpair(sam_file):
    # Determine output file name
    out_bed_pair = re.sub(r'^.+/', '', sam_file)
    out_bed_pair = re.sub(r'sam$', 'bedpair', out_bed_pair)

    try:
        with open(sam_file, 'r') as sam, open(out_bed_pair, 'w') as out:
            while True:
                frag_a = sam.readline()
                if not frag_a:
                    break
                if frag_a.startswith('@'):
                    continue
                frag_b = sam.readline()

                sub_a = frag_a.split()
                sub_b = frag_b.split()
                id_a_info = sub_a[0].split('_')
                id_b_info = sub_b[0].split('_')
                sample_a = id_a_info.pop(0)
                sample_b = id_b_info.pop(0)
                strand_a = id_a_info[1]
                strand_b = id_b_info[1]

                if id_a_info[0] != id_b_info[0]:
                    print(frag_a, frag_b)
                    raise ValueError("did not belong to the same pair")

                chr_a = sub_a[2]
                loci_a = int(sub_a[3])
                cigar_a = sub_a[5]
                match_a = int(re.search(r'(\d+)M', cigar_a).group(1))

                chr_b = sub_b[2]
                loci_b = int(sub_b[3])
                cigar_b = sub_b[5]
                match_b = int(re.search(r'(\d+)M', cigar_b).group(1))

                start_a = loci_a
                end_a = loci_a + match_a - 1
                start_b = loci_b
                end_b = loci_b + match_b - 1

                read_a_info = f"{chr_a}\t{start_a}\t{end_a}"
                read_b_info = f"{chr_b}\t{start_b}\t{end_b}"

                if strand_a == "Plus":
                    real_strand_a = "+"
                elif strand_a == "Minus":
                    real_strand_a = "-"
                else:
                    raise ValueError("wrong format1")

                if strand_b == "Plus":
                    real_strand_b = "+"
                elif strand_b == "Minus":
                    real_strand_b = "-"
                else:
                    raise ValueError("wrong format2")

                if chr_a == chr_b:
                    if start_a < start_b:
                        out.write(f"{read_a_info}\t{read_b_info}\t{sample_a}_{id_a_info[0]}_{id_a_info[1]}\t60\t{real_strand_a}\t{real_strand_b}\n")
                    else:
                        out.write(f"{read_b_info}\t{read_a_info}\t{sample_a}_{id_a_info[0]}_{id_a_info[1]}\t60\t{real_strand_b}\t{real_strand_a}\n")
                elif chr_a < chr_b:
                    out.write(f"{read_a_info}\t{read_b_info}\t{sample_a}_{id_a_info[0]}_{id_a_info[1]}\t60\t{real_strand_a}\t{real_strand_b}\n")
                else:
                    out.write(f"{read_b_info}\t{read_a_info}\t{sample_a}_{id_a_info[0]}_{id_a_info[1]}\t60\t{real_strand_b}\t{real_strand_a}\n")

    except Exception as e:
        print(e)

# Example usage
sam_to_bedpair('interaction_merge.intraMolecular.Chimeric.sam')


#output interaction_merge.intraMolecular.Chimeric.bedpair
commands = ['rm pairreads_distance_in_mature_trans.list']



'''commands = ['rm interaction_merge.intraMolecular.Chimeric.sam']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")'''

'commands = [\'rm interaction_merge.intraMolecular.Chimeric.sam\']\nfor command in commands:\n    subprocess.run(command, shell=True, check=True)\n    print(f"Command \'{command}\' executed successfully.")'

In [69]:
# unique_then_merge_with_newID.pl


def process_bedpair_file(input_file):
    output_file = 'interaction.merged.intraChimeric.uniq.bedpair'
    unique = {}

    prefix = re.sub(r'\.merged\.intraChimeric\.bedpair$', '', input_file)

    try:
        with open(input_file, 'r') as bf, open(output_file, 'w') as out:
            for line in bf:
                line = line.strip()
                sub = line.split()
                sub[6] = f"{prefix}#{sub[6]}"

                '''# Unique
                scale = 5
                left_start = int(sub[1]) // scale
                left_end = (int(sub[2]) // scale) + (1 if int(sub[2]) % scale else 0)
                right_start = int(sub[4]) // scale
                right_end = (int(sub[5]) // scale) + (1 if int(sub[5]) % scale else 0)'''
                
                ##############################################################################
                left_start = int(sub[1])
                left_end = int(sub[2])
                right_start = int(sub[4])
                right_end = int(sub[5]) 
                ##
                
                pair_info = [f"{sub[0]}\t{left_start}\t{left_end}", f"{sub[3]}\t{right_start}\t{right_end}"]
                pair_info.sort()
                tmp_pair_info = "\t".join(pair_info)

                if unique.get(tmp_pair_info, 0) >= 2:  # Keep two pairs
                    continue

                unique[tmp_pair_info] = unique.get(tmp_pair_info, 0) + 1

                # Output
                ##############################################################################################
                scale=1
                sub[1] = scale * left_start
                sub[2] = scale * left_end
                sub[4] = scale * right_start
                sub[5] = scale * right_end
                new_line = "\t".join(map(str, sub))
                out.write(new_line + "\n")

    except Exception as e:
        print(e)


# Example usage
process_bedpair_file('interaction_merge.intraMolecular.Chimeric.bedpair')

#output interaction.merged.intraChimeric.uniq.bedpair



commands = ['rm interaction_merge.intraMolecular.Chimeric.bedpair']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

Command 'rm interaction_merge.intraMolecular.Chimeric.bedpair' executed successfully.


In [70]:
#skipping clustering?

def process_and_remove_lines(input_file, output_file):
        with open(input_file, 'r') as ipp, open(output_file, 'w') as out_file:
            out_file.write("track graphType=arc\n")
            for line in ipp:
                line = line.strip()
                sub = line.split()
                if int(sub[2])<int(sub[4]):
                    out_file.write(f"{sub[0]}\t{sub[2]}\t{sub[4]}\n")
                else:
                    print(sub)
                    
                    out_file.write(f"{sub[0]}\t{sub[4]}\t{sub[2]}\n")

# Usage
process_and_remove_lines('interaction.merged.intraChimeric.uniq.bedpair', f'{output_bed_final}')
# cp output.no.clustering.bed /mnt/c/Users/99alb/OneDrive/Desktop/.




commands = ['rm interaction.merged.intraChimeric.uniq.bedpair']
for command in commands:
    subprocess.run(command, shell=True, check=True)
    print(f"Command '{command}' executed successfully.")

['NC_000913.3', '3517505', '3517579', 'NC_000913.3', '3517578', '3517653', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_474_Minus', '60', '-', '-']
['NC_000913.3', '2111181', '2111256', 'NC_000913.3', '2111253', '2111328', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_1282_Minus', '60', '-', '-']
['NC_000913.3', '3072770', '3072845', 'NC_000913.3', '3072839', '3072914', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_2230_Minus', '60', '-', '-']
['NC_000913.3', '1490453', '1490528', 'NC_000913.3', '1490521', '1490596', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_2285_Minus', '60', '-', '-']
['NC_000913.3', '2032070', '2032144', 'NC_000913.3', '2032141', '2032216', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_2552_Minus', '60', '-', '-']
['NC_000913.3', '1915145', '1915220', 'NC_000913.3', '1915210', '1915285', 'interaction_merge.intraMolecular.Chimeric.bedpair#AlignPairWhole_2913_Minus